In [11]:
from vidigi.utils import EventPosition, create_event_position_df
from vidigi.prep import reshape_for_animations, generate_animation_df
from vidigi.animation import generate_animation, animate_activity_log
import pandas as pd
import os
import random
import plotly.io as pio
pio.renderers.default = "notebook"

In [12]:
#| echo: false
#| output: asis
# Path to the external Python script
file_path = "simpy_gas_stations.py"

# Read the file content
if os.path.exists(file_path):
    with open(file_path, "r") as f:
        code_content = f.read()
else:
    code_content = "File not found."
with open(file_path, "r") as f:
    code_content = f.read()

# Print the Quarto `{details}` block for collapsible output
print(f"""
:::{{.callout-note collapse="true"}}
### View Imported Code, which has had logging steps added at the appropriate points in the 'model' class

```python
{code_content}
```

:::

""")


:::{.callout-note collapse="true"}
### View Imported Code, which has had logging steps added at the appropriate points in the 'model' class

```python
"""
Gas Station Refueling example

Covers:

- Resources: Resource
- Resources: Container
- Waiting for other processes

Scenario:
  A gas station has a limited number of gas pumps that share a common
  fuel reservoir. Cars randomly arrive at the gas station, request one
  of the fuel pumps and start refueling from that reservoir.

  A gas station control process observes the gas station's fuel level
  and calls a tank truck for refueling if the station's level drops
  below a threshold.

"""

import itertools
import random

from vidigi.resources import VidigiStore
from vidigi.animation import animate_activity_log
from vidigi.logging import EventLogger
from vidigi.utils import EventPosition, create_event_position_df

import simpy

# fmt: off
RANDOM_SEED = 42
STATION_TANK_SIZE = 400    # MODIFIED FROM EXAMPLE: Size of the gas station tank

In [13]:
# Define positions for animation
event_positions = create_event_position_df([
    EventPosition(event='arrival', x=0, y=350, label="Entrance"),
    EventPosition(event='pump_queue_wait_begins', x=400, y=400, label="Queue"),
    EventPosition(event='payment_begins', x=340, y=150, resource='num_pumps',
                  label="Pumping Gas"),
    EventPosition(event='pumping_begins', x=340, y=150, resource='num_pumps',
                  label="Pumping Gas"),
    EventPosition(event='calling_truck', x=140, y=50,
                  label="Calling Truck"),
        EventPosition(event='refueling', x=340, y=50,
                  label="Truck Filling Tank"),
    EventPosition(event='depart', x=250, y=50, label="Exit")
])

class Params:
    def __init__(self):
        self.num_pumps = 2

icon_list = [ "🚗", "🚙", "🚓",
            "🚗", "🚙", "🏍️", "🏍️",
            "🚗", "🚙", "🚑",
            "🚗", "🚙", "🛻",
            "🚗", "🚙", "🚛",
            "🚗", "🚙", "🚕",
            "🚗", "🚙", "🚒",
            "🚗", "🚙", "🚑"]

random.shuffle(icon_list)

In [14]:
event_log_df = pd.read_csv("gas_station_log.csv")

In [15]:
STEP_SNAPSHOT_MAX = 6
LIMIT_DURATION = 60*60*3
WRAP_QUEUES_AT = 3

In [21]:
full_entity_df = reshape_for_animations(
    event_log=event_log_df,
    every_x_time_units=5,
    step_snapshot_max=STEP_SNAPSHOT_MAX,
    limit_duration=LIMIT_DURATION,
    debug_mode=True
    )

full_entity_df_plus_pos = generate_animation_df(
    full_entity_df=full_entity_df,
    event_position_df=event_positions,
    wrap_queues_at=WRAP_QUEUES_AT,
    step_snapshot_max=STEP_SNAPSHOT_MAX,
    gap_between_entities=150,
    gap_between_resources=180,
    gap_between_queue_rows=150,
    # gap_between_resource_rows=60,
    debug_mode=True,
    custom_entity_icon_list=icon_list
    )


Iteration through time-unit-by-time-unit logs complete 23:24:54
Snapshot df concatenation complete at 23:24:55
Placement dataframe finished construction at 23:24:55


In [22]:
def build_fuel_bar(value, max_value=50, length=10):
    """Create an ASCII bar to show fuel level."""
    try:
        if value is None or (isinstance(value, float) and (value != value)):  # check for None or NaN
            proportion = 0
        else:
            proportion = min(max(value / max_value, 0), 1)
    except Exception:
        proportion = 0  # fallback

    filled = int(proportion * length)
    empty = length - filled
    filled_icon = "█"
    empty_icon = "░"
    return "[" + filled_icon * filled + empty_icon * empty + "]"


In [23]:
def custom_icon_rules(row):
    icon = row.get("icon", "")
    entity_id = row.get("entity_id", "")
    event = row.get("event", "")
    fuel_level_start = row.get("fuel_level_start", None)  # Only for cars

    if "more" not in str(icon):
        if isinstance(entity_id, str):
            if "Truck" in entity_id:
                return "🚚 Truck is<br>refilling the tank..."
            elif "Call" in entity_id:
                return "☎️ Calling Truck!"
            elif "Car" in entity_id:
                bar = ""
                if (event == "arrival" or event == "pump_queue_wait_begins") and fuel_level_start is not None:
                    bar = " " + build_fuel_bar(fuel_level_start)
                    return icon + "<br>" + bar + "<br><br>"
                elif event == "payment_begins" and fuel_level_start is not None:
                    bar = " " + build_fuel_bar(fuel_level_start)
                    return icon+ "<br>" + bar + "<br> Paying"
                elif event == "pumping_begins" and fuel_level_start is not None:
                    arrival_time = row["time"]
                    elapsed = max(float(row["snapshot_time"]) - float(arrival_time), 0)
                    current_fuel = min(fuel_level_start + elapsed * 1, 50)
                    bar = " " + build_fuel_bar(current_fuel)
                    return icon+ "<br>" + bar + "<br> Pumping"
                elif event == "departure" or event == "pumping_ends":
                    bar = " " + build_fuel_bar(50)  # Car is full when it leaves
                    return icon+ "<br>" + bar + "<br> <br>"


            else:
                return icon
    return icon


full_entity_df_plus_pos = full_entity_df_plus_pos.assign(
            icon=full_entity_df_plus_pos.apply(custom_icon_rules, axis=1)
            )

In [26]:
generate_animation(
        full_entity_df_plus_pos=full_entity_df_plus_pos.sort_values(['entity_id', 'snapshot_time']),
        event_position_df= event_positions,
        scenario=Params(),
        simulation_time_unit="seconds",
        plotly_height=900,
        plotly_width=1200,
        override_x_max=500,
        override_y_max=750,
        entity_icon_size=30,
        gap_between_resources=180,
        display_stage_labels=False,
        # resource_opacity=1,
        resource_opacity=0,
        setup_mode=False,
        # custom_resource_icon="⛽",
        resource_icon_size=40,
        add_background_image="https://raw.githubusercontent.com/hsma-tools/vidigi/refs/heads/main/examples/example_15_gas_station_refuelling/gas_station.png",
        background_image_opacity=1, # New parameter in 1.1.0
        overflow_text_color="white", # New parameter in 1.1.0
        start_time="09:00:00",
        time_display_units="%H:%M:%S",
        debug_mode=True,
        frame_duration=100,
        frame_transition_duration=100
    )

Output animation generation complete at 23:26:26


In [27]:
import plotly.express as px

fuel_level_change_df = event_log_df[(event_log_df["event_type"]=="fuel_level_change") &
                                    (event_log_df["time"] % 5 == 0)]

px.bar(fuel_level_change_df, x="entity_id", y="value", animation_frame="time", range_y=[0,400])